# CMSE/MTH 401 - Example Midterm (Spring 2019)
This is an open internet exam.  Feel free to use anything on the internet with one important exception...

- **DO NOT** communicate live with other people during the exam (either verbally or on-line).  The goal here is to find answers to problems as you would in the real world.  

You will be given **60 minutes (wishful thinking by the instructor, you will be given the entire exam time if needed)** to complete this test.  Use your time wisely. 

**HINTS:**
- Neatness is important.  we will ignore all notes or code we can not read. 
- Read the entire exam from beginning to end before starting.  Not all questions are equal in points vs. time so plan your time accordingly.   
- Skip questions you can not answer. 
- Some of the information provided my be a distraction. Do not assume you need to understand everything written to answer the questions. 
- Spaces for answers are provided. Delete the prompting text such as "Put your answer to the above question here" and replace it with your answer. Do not leave the prompting text with your answer.
- Do not assume that the answer must be in the same format of the cell provided. Feel free to change the cell formatting (ex. markdown to code) or add additional cells as needed to provide your answer.
- When we say "in your own words" it is still okay to search the Internet for the answer as a reminder, however, we would like you to do more than cut and paste.  Make the answer your own. 
- If you get stuck, try not to leave an answer blank. It is better to include some notes or stub functions so we have an idea about your thinking process so we can give you partial credit.   
- Always provided links to any references you find helpful. 
- Feel free to delete the provided check marks (&#9989;) as a way to keep track of which questions you have successfully completed. 



### Exam Summary
1. (25 points) [Conways Game of Life](#gol)
2. (25 points) [Job Scheduling](#jobs)
2. (25 points) [CUDA](#CUDA)
3. (25 points) [OpenMM](#OpenMM)

---

<a name="gol"></a>
# Question 1 - (25 points) Conways Game of Life

<img alt="animated game of life image"
     src="https://upload.wikimedia.org/wikipedia/commons/e/e5/Gospers_glider_gun.gif">

[Glider Generator Example from Wikipedia](https://en.wikipedia.org/wiki/Conway%27s_Game_of_Life)

> The Game of Life, also known simply as Life, is a cellular automaton devised by the British mathematician John Horton Conway in 1970.
> 
> The game is a zero-player game, meaning that its evolution is determined by its initial state, requiring no further input. One interacts with the Game of Life by creating an initial configuration and observing how it evolves, or, for advanced players, by creating patterns with particular properties.
> 
> The universe of the Game of Life is an infinite, two-dimensional orthogonal grid of square cells, each of which is in one of two possible states, alive or dead, (or populated and unpopulated, respectively). Every cell interacts with its eight neighbours, which are the cells that are horizontally, vertically, or diagonally adjacent. At each step in time, the following transitions occur:
> 
> - Any live cell with fewer than two (<2) live neighbours dies, as if by underpopulation.
> - Any live cell with two or three [2-3) live neighbours lives on to the next generation.
> - Any live cell with more than three (>3) live neighbours dies, as if by overpopulation.
> - Any dead cell with exactly three (3) live neighbours becomes a live cell, as if by reproduction.
> 
> The initial pattern constitutes the seed of the system. The first generation is created by applying the above rules simultaneously to every cell in the seed; births and deaths occur simultaneously, and the discrete moment at which this happens is sometimes called a tick. Each generation is a pure function of the preceding one. The rules continue to be applied repeatedly to create further generations.

The game of life is used as a model in a number of different scientific domains.  The following code is an OpenMP implamentation of Conway's Game of life. Use the code as a reference and answer the questions below. This example comes from here: http://ernie55ernie.github.io/parallel%20programming/2016/03/25/openmp-game-of-life.html

```c++
#include <stdio.h>
#include <string.h>
#include <omp.h>
#include <stdlib.h>
#include <assert.h>
#define MAX_N 2000

int plate[2][(MAX_N + 2) * (MAX_N + 2)];
int which = 0;
int n;
int live(int index){
	return (plate[which][index - n - 3] 
		+ plate[which][index - n - 2]
		+ plate[which][index - n - 1]
		+ plate[which][index - 1]
		+ plate[which][index + 1]
		+ plate[which][index + n + 1]
		+ plate[which][index + n + 2]
		+ plate[which][index + n + 3]);
}
void iteration(){
#pragma omp parallel for schedule(static)
	for(int i = 1; i <= n; i++){
		for(int j = 1; j <= n; j++){
			int index = i * (n + 2) + j;
			int num = live(index);
			if(plate[which][index]){
				plate[!which][index] =  (num == 2 || num == 3) ?
					1 : 0;
			}else{
				plate[!which][index] = (num == 3);
			}
		}
	}
	which = !which;
}
void print_plate(){
	for(int i = 1; i <= n; i++){
		for(int j = 1; j <= n; j++){
			printf("%d", plate[which][i * (n + 2) + j]);
		}
		printf("\n");
	}
	printf("\0");
}
int main(){
	int M;
	char line[MAX_N];
	memset(plate[0], 0, sizeof(int) * (n + 2) * (n + 2));
	memset(plate[1], 0, sizeof(int) * (n + 2) * (n + 2));
	if(scanf("%d %d", &n, &M) == 2){
		for(int i = 1; i <= n; i++){
			scanf("%s", &line);
			for(int j = 0; j < n; j++){
				plate[0][i * (n + 2) + j + 1] = line[j] - '0';
			}
		}
		for(int i = 0; i < M; i++){
			iteration();
		}
		print_plate();
	}
	return 0;
}
```

### Step 1.a: Compiling the code

&#9989; **<font color=red>Question 1.a</font>**: Assume that the above code is stored in a file named ```game_of_life.c```, in your current directory.  What command(s) are needed to compile the code (with OpenMP and level 3 optimization) on a dev node and make an executable named ```gol```.

### Step 1.b: Formatting the input

When compiled the above program can be run using the following command:

```gol < data```


The input, ```data```, is an input file with the following example syntax:

```
5 1
10001
00100
01110
00100
01010
```

The first line is two integer, $N$ and $M$, indicating the the ```world``` is of size $N \times N$ and modeling cycles is $M$. The following are $N$ lines with $N$ numbers on each line, where 0 indicates the cell is dead and 1 is live.

&#9989; **<font color=red>Question 1.b:</font>**: In class we talked about the "grater than" (```>```) character which redirects the output from the terminal to a file.  In your own words, what does the "less than" ```<``` character do in BASH?

Put the answer to the above question here

### Step 1.c: Analyzing the code

&#9989; **<font color=red>Question 1.c</font>**: Explain why the code will slow down if you changed the OpenMP scheduling from ```static``` to ``dynamic``?

Put the answer to the above question here

&#9989; **<font color=red>Question 1.d</font>**: Observe that the ```plate``` is initialized with two (2) $N \times N$ worlds and switches between them using the ```which``` variable after every cycle.  What common parallelization problem is avoided by having two arrays instead of one? Explain your answer.

Put the answer to the above question here

&#9989; **<font color=red>Question 1.e</font>**: Assume a largish grid size ($N$) running over a very long number of cycles ($M$) takes 2 days to run on a single core. What is the minimum estimated time (in minutes) that an OpenMP version of this could run on a 40 core machine? Make sure you explain your answer or show your work.

Put the answer to the above question here

----
<a name="jobs"></a>
# Question 2 - (25 points) Job Scheduling

<a title="SimpleIcon http://www.simpleicon.com/ [CC BY 3.0 (https://creativecommons.org/licenses/by/3.0)], via Wikimedia Commons" href="https://commons.wikimedia.org/wiki/File:Simpleicons_Business_calendar-check.svg"><img width="256" alt="Simpleicons Business calendar-check" src="https://upload.wikimedia.org/wikipedia/commons/thumb/5/5a/Simpleicons_Business_calendar-check.svg/256px-Simpleicons_Business_calendar-check.svg.png"></a>

Assume the following SLURM submission script is named ```gol_array.sb``` and is in your current directory on the HPCC:

```bash
#!/bin/bash -login
#SBATCH --time=02:00:00
#SBATCH --mem=2GB
#SBATCH --nodes=1
#SBATCH --ntasks-per-node=40
#SBATCH --array=1-10

module load powertools

time gol < data.${SLURM_JOBID} > output.${SLURM_JOBID}

js ${SLURM_JOBID}

```

In addition to the above script there is also a command named ```gol``` and one hundred (100) input files of the form ```data.1``` though ```data.100``` in your current directory.

**<font color=red>Question 2.a:</font>** The above script tries to use a concept called a "Job Array" to submit more than one identical job to the cluster with a single command.  Find a reference that describes how to use SLURM job arrays.  Include a link to the reference as your answer to 2.a. 

**<font color=red>Question 2.b:</font>** What command should you use to submit the script (as is) to the cluster?

&#9989; **<font color=red>Question 2.c</font>**: When you try to run the above script the system only produces one output file with the name ```output.12741266``` (you were expecting 100 files).  You notice that the script is using the wrong environment variable for the input and output files.  What variable should be used to indicate the array TASK ID instead of the JOB ID? Rewrite the ```time gol...``` line from the above script to use the correct variable.

Put the answer to the above question here

&#9989; **<font color=red>Question 2.d</font>**: After fixing the code using the correct environment variable. Rerunning the submission script produces the following files: ```output.1```, ```output.2```, ```output.3```, ```output.4```, ```output.5```, ```output.6```, ```output.7```, ```output.8```, ```output.9```, ```output.10```.  All of these seem right but you are still expecting 100 output files.  How do you modify the submission script to run all jobs from 1 to 100?

&#9989; **<font color=red>Question 1.e:</font>**: You use job arrays when your jobs are "pleasantly parallel" and can be run in any order.  Assuming that the cluster has 12 nodes with 40 cores in each node. Also assume that each job in the array will use all of the resources requested in the script.  What is the fastest that the entire array will complete on the cluster? Explain your answer.

Put the answer to the above question here

---
<a name="CUDA"></a>

# Question 3 - (25 points) CUDA

<img src="https://www.bogotobogo.com/Matlab/images/ImageProcessing_6_Low_Pass_Filter/disk_filter.png" width="65%">

Consider the following code snip-it similar to the Average Filter loop from Homework 4.  

```c++

int nBytes = sz.width*sz.height*channels*sizeof(char));
char * s_img = (char *) malloc(nBytes);
char * o_img = (char *) malloc(nBytes);

//make 2D pointer arrays from 1D image arrays
char **img = malloc(sz.height * sizeof(char*));
for (int r=0; r<sz.height; r++)
        img[r] = &s_img[r*sz.width];
char **output = malloc(sz.height * sizeof(char*));
for (int r=0; r<sz.height; r++)
        output[r] = &o_img[r*sz.width];

//average filter
for(int c=0;c<sz.width;c++) 
    for(int r=0;r<sz.height;r++)
    {
        double count = 0;
        double tot = 0;
        for(int cw=max(0,c-halfwindow); cw<min(sz.width,c+halfwindow+1); cw++)
            for(int rw=max(0,r-halfwindow); rw<min(sz.height,r+halfwindow+1); rw++)
            {
                count++;
                tot += (double) img[rw][cw];
            }
        output[r][c] = (int) (tot/count);
    }
```

The following is an attempt to replace the above loop with a cuda kernel funciton

```c++

__global__ void average_im( char * img_d, 
                            char * output_d, 
                            int sz_width, 
                            int sz_height, 
                            int halfwindow) {

    int c = blockIdx.x * BLOCKDIM + threadIdx.x;
    int r = blockIdx.y * BLOCKDIM + threadIdx.y;
    int i = r*sz_width+c;
    
    if (c < sz_width && r < sz_height) 
    {
        int count = 0;
        int tot = 0;
        int c_start = fmax(0,c-halfwindow);
        int c_stop = fmin(sz_width,c+halfwindow+1);
        int r_start = fmax(0,r-halfwindow);
        int r_stop = fmin(sz_height,r+halfwindow+1);
        for(int cw=c_start; cw<c_stop; cw++)
            for(int rw=r_start; rw<r_stop; rw++)
            {
                count++;
                tot += img_d[i];
            }
        output_d[i] = (int) (tot/count);
    }
}
```

&#9989; **<font color=red>Question 3.a</font>**: Assuming the above CUDA function compiles properly, the function can be called using the following lines of code:

```c++
average_im<<<numBlocks, numThreads>>>(img_d,output_d,sz.width,sz.height, halfwindow)
    
cudaError_t err = cudaGetLastError();
if (err != cudaSuccess) {
    fprintf(stderr, "\n\nError: %s\n\n", cudaGetErrorString(err)); fflush(stderr); exit(err);   
}
```

Write the lines of code needed to declare ```numBLocks``` and ```numThreads``` before making the above call.  Make sure that there are an equal number of threads in the x and y direction of the block and that the block uses the maximum number of threads. 

&#9989; **<font color=red>Question 3.b</font>**:  Now, go back and write the code needed to declare and allocate the space for ```img_d``` and ```output_d``` on the GPU. You can  assume the ```CUDA_CALL``` macro we used in class is already defined.

&#9989; **<font color=red>Question 3.c</font>**:  Write the command to copy the image file from the host to the gpu device and into the ```img_d``` variable. You can still assume the ```CUDA_CALL``` macro we used in class is already defined.

&#9989; **<font color=red>Question 3.d</font>**: This kernel function could benefit from shared memory tiling. Identify the data you would need to copy to shared memory to implement tiling. Write the line of code that you would need to add to the above function to declare the local variable(s) in shared memory?  (**HINT**: Do not implement shared memory tiling, I just want to see if you understand which data you would use and the syntax for declaring the variable to be shared by a block of threads).  

Put your answer to the above question here

&#9989; **<font color=red>Question 3.e</font>**:  Name two (or more) specific programming concepts (not counting tiling) that you could use to speed up the above CUDA kernel? Be clear in your answer and make sure you are explicit in defining two separate concepts for this kernel (for example, "Improve the algorithm" and "reduce memory access speeds" are too general and would work for any kernel). 

----
<a name="OpenMM"></a>

# Question 4 - (25 points)  OpenMM

<img src="http://openmm.org/img/logos/Icon.svg" width="30%">

OpenMM is a high performance (aka parallel) toolkit for molecular simulation.  Do some internet research on OpenMM, read about it and answer the following questions. 

&#9989; **<font color=red>Question 4.a:</font>** What type of parallelization does OpenMM use (ex. Shared Memory, Shared Network, GPUs, Other)?  Include a link or explain where you found the answer.  

Put your answer to the above question here.

&#9989; **<font color=red>Question 4.b:</font>** The interface for OpenMM is written in Python.  How does OpenMM avoid problems with serialization of the code due to the Global Interpreter Lock (GIL)?

Put your answer to the above question here.

&#9989; **<font color=red>Question 4.c:</font>** What command would you use to search for OpenMM in the HPCC module system?

Put your answer to the above question here.

&#9989; **<font color=red>Question 4.d:</font>** What versions (if any) of OpenMM are installed on the HPCC and are available in the module system? 

Put your answer to the above question here.

&#9989; **<font color=red>Question 4.e:</font>** Assume you have an OpenMM job running on the HPCC with Job number 7848455 and there is something wrong.  What command would you use to stop the job?

Put your answer to the above question here.

---------
### Congratulations, you're done with your EXAM

Now, you just need to submit this assignment by uploading it to the course <a href="https://d2l.msu.edu/">Desire2Learn</a> web page for today's dropbox.

&#9989; **<font color=red>DO THIS:</font>**
- Download the Notebook to your desktop with the filename using the format **"<NETID\>_Midterm-Exam.ipynb"**.  Replace <NETID\> in the filename with your personal MSU NetID (the stuff that comes before the @ symbol in your msu email address).
- Upload the newly renamed notebook to the D2L dropbox. 


Written by Dr. Dirk Colbry, Michigan State University
<a rel="license" href="http://creativecommons.org/licenses/by-nc/4.0/"><img alt="Creative Commons License" style="border-width:0" src="https://i.creativecommons.org/l/by-nc/4.0/88x31.png" /></a><br />This work is licensed under a <a rel="license" href="http://creativecommons.org/licenses/by-nc/4.0/">Creative Commons Attribution-NonCommercial 4.0 International License</a>.

&#169; Copyright 2019,  Michigan State University Board of Trustees